In [1]:
!pip install -q transformers sentence-transformers faiss-cpu datasets accelerate bitsandbytes


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.4/31.4 MB 66.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.1/60.1 MB 25.9 MB/s eta 0:00:00


In [30]:

from transformers import pipeline
pipe = pipeline(
    "text-generation",
    model="mistralai/Mistral-7B-Instruct-v0.2",  # tested public model
    device_map="auto",
    torch_dtype="auto"

)

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

Device set to use cuda:0


In [9]:
from datasets import load_dataset
ds = load_dataset("allenai/c4", "realnewslike", split="train[:1%]")
docs = [d["text"] for d in ds if d["text"]]
print(len(docs))


README.md: 0.00B [00:00, ?B/s]

Resolving data files:   0%|          | 0/1024 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/512 [00:00<?, ?it/s]

realnewslike/c4-train.00000-of-00512.jso(…):   0%|          | 0.00/30.1M [00:00<?, ?B/s]

realnewslike/c4-train.00001-of-00512.jso(…):   0%|          | 0.00/30.1M [00:00<?, ?B/s]

...

realnewslike/c4-train.00511-of-00512.jso(…):   0%|          | 0.00/29.9M [00:00<?, ?B/s]

realnewslike/c4-validation.00000-of-0000(…):   0%|          | 0.00/15.3M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/13799838 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/13863 [00:00<?, ? examples/s]

137998


In [10]:
from sentence_transformers import SentenceTransformer
import numpy as np, faiss, gc

embedder = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = embedder.encode(docs, batch_size=64,
                              show_progress_bar=True, convert_to_numpy=True)

index = faiss.IndexFlatL2(embeddings.shape[1])
index.add(embeddings)
gc.collect()

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

...

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Batches:   0%|          | 0/2157 [00:00<?, ?it/s]

17

In [24]:
def retrieve(query, k=10):
    q_emb = embedder.encode([query], convert_to_numpy=True)
    D, I = index.search(q_emb, k)
    return [docs[i] for i in I[0]]

In [34]:
def agentic_rag_stub(query):
    prompt = f"Answer in detail: {query}"
    out = pipe(prompt, max_new_tokens=200, temperature=0.7, top_p=0.9)
    return out[0]["generated_text"]

print(agentic_rag_stub("Tell me a quantization technique better than LoRA"))

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


Answer in detail: Tell me a quantization technique better than LoRA?

LoRa (Long Range) is a wireless communication protocol designed for long-range, low-power applications, particularly in the Internet of Things (IoT) domain. It's known for its long-range capabilities and low power consumption. However, when it comes to quantization techniques, LoRa itself doesn't provide any advanced quantization methods. Instead, it relies on the application or the data processing unit to implement suitable quantization techniques.

One quantization technique that could be considered better than LoRa, depending on the specific use case, is Delta-Sigma Modulation (DSM). DSM is a type of oversampling delta modulation technique that converts continuous-time signals into digital form with high resolution and low quantization error.

Delta-Sigma Modulation has several advantages over other quantization techniques:

1. High Resolution: DSM can provide higher resolution than other quantization techniques w

In [31]:
def rag_pipeline(query, k=5):
    # Retrieve relevant documents
    retrieved_docs = retrieve(query, k)

    # Create a prompt with the retrieved documents
    context = "\n".join(retrieved_docs)
    prompt = f"Given the following context, answer the query in detail:\n\nContext:\n{context}\n\nQuery: {query}"

    # Generate the answer using the text generation pipeline
    out = pipe(prompt, max_new_tokens=500, temperature=0.7, top_p=0.9)
    return out[0]["generated_text"]

In [35]:
query = "is there an significant evnts before 10/11?"
answer = rag_pipeline(query)
print(answer)

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


Given the following context, answer the query in detail:

Context:
AUDJPY posted hefty losses after rising to a five-month peak of 83.90 in early December, falling back below its 200-day simple moving average (SMA) to find support near its 50-day SMA. The pair is now trading at a one-month low, and the short-term bias seems to have shifted back to negative, though a decisive close below the 50-day SMA is needed to confirm that.
Short-term oscillators support the notion, as the RSI just dipped below its neutral 50 line, while the MACD recently crossed beneath its red trigger line; a bearish signal.
Further declines could encounter support near the 80.47 zone, marked by the peaks of October 19. Even lower, the October 25 top of 79.80 would come into view, a level much more visible on the 4-hour chart. Lower still, buy orders may be found near the round figure of 79.00.
On the upside, a first wave of resistance to advances may come at 81.40, the November 23 trough. A bullish break would o